<a href="https://githubtocolab.com/mehak-sachdeva/ASU-GIS-322-Fall-19/blob/master/notebooks/6_2_Adding_a_web_basemap_using_Folium.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 6.2 Adding a web basemap using Folium

<br></br>
The idea of using `Folium` is to add a web basemap to give your map visulization a little more context. For example, if you present your Phoenix crime map to someone who are not familiar with Phoenix, they might get lost about where is where. So, by adding a basemap such as Google Maps or OpenStreetMap, it will make much easier for the person who is reading your map.

<br></br>
First of all, let's get a feel about it!

In [0]:
import folium

<br></br>
`folium.Map()`  gives us the basemap at a given location. In this example, I use a location with longitude of -111.9400 and latitude of 33.4255.

In [0]:
folium.Map(location=[33.4255, -111.9400])

In [0]:
help(folium.Map)

Help on class Map in module folium.folium:

class Map(branca.element.MacroElement)
 |  Create a Map with Folium and Leaflet.js
 |  
 |  Generate a base map of given width and height with either default
 |  tilesets or a custom tileset URL. The following tilesets are built-in
 |  to Folium. Pass any of the following to the "tiles" keyword:
 |  
 |      - "OpenStreetMap"
 |      - "Mapbox Bright" (Limited levels of zoom for free tiles)
 |      - "Mapbox Control Room" (Limited levels of zoom for free tiles)
 |      - "Stamen" (Terrain, Toner, and Watercolor)
 |      - "Cloudmade" (Must pass API key)
 |      - "Mapbox" (Must pass API key)
 |      - "CartoDB" (positron and dark_matter)
 |  
 |  You can pass a custom tileset to Folium by passing a Leaflet-style
 |  URL to the tiles parameter: ``http://{s}.yourtiles.com/{z}/{x}/{y}.png``
 |  
 |  Parameters
 |  ----------
 |  location: tuple or list, default None
 |      Latitude and Longitude of Map (Northing, Easting).
 |  width: pixel int 

Check out the parameters in folumn.Map()

<br></br>
As you can see, there are many parameters in the `folium.Map()` method. For example, besides location, we can specify the 
style of the map, the zoom level and the size of the map.

In [0]:
asu = folium.Map(
    location=[33.4200, -111.9350],
    tiles='Stamen Toner',
    zoom_start=15,
    width=1000, 
    height=400
)
asu

<br></br>
We can also add some markers to the asu map by using `folium.Marker().add_to(asu)`. Here, I added two locations on campus.

In [0]:
!pip install geopandas
import geopandas as gpd
phx_crimes = gpd.read_file("phoenix_crime_counts.shp")

In [0]:
folium.Marker([33.419536, -111.937902], popup='<i>COOR Hall</i>').add_to(asu)
folium.Marker([33.415721, -111.932012], popup='<b>Gym</b>').add_to(asu)
asu

<br></br>
How about overlaying our Phoenix Crime Map? Let's read in our `phoenix_crime_counts.shp`.

In [0]:
phx_crimes.crs

{'init': 'epsg:4269'}

<br></br>
Remember our origin projection is latitude and longitude ('epsg:4269'), and We need to convert it to the web mercator which is 'epsg:4326'. It is very important to let your GeoDataFrame to have the web mercator projection in order to be displayed properly.

<br></br>
Next we need to use `.to_json` command to convert the `GeoDataFrame` to the `geojson` format that `folium` supports.

In [0]:
phx_crimes_json = phx_crimes.to_crs(epsg='4326').to_json()

<br></br>
Let's create a basemap first with proper zoom-level (feel free to play around with the zoom-level).

In [0]:
crime_map = folium.Map(location=[33.4255, -111.9400], zoom_start=9)

<br></br>
Then we need to use the `geojson` file to make a `folium.Choropleth` Map. Below are the commands.

In [0]:
folium.Choropleth(
    geo_data=phx_crimes_json,
    name='Phoenix Crime Counts', # 
    data=phx_crimes, #Our GeoDataFrame
    columns=['Zipcode','INC NUMBER'], #
    key_on='feature.properties.{}'.format('Zipcode'), #we need to specify a unique key for each zipcode
    fill_color='RdBu_r', #fill color, here I'm using blue to red
    fill_opacity=0.7, # opacity of the polygon fill color
    line_opacity=0.2, # opacity of the boundary line
    legend_name='counts', #legend name
    highlight = True, #Hover to highlight
    control = True
).add_to(crime_map)

crime_map

<br></br>
We can also add a `folium.LayerControl()` to our `crime_map` so that we can toggle layers. Note there will be small button on the top-left corner of your map.

In [0]:
folium.LayerControl().add_to(crime_map)
crime_map

<br></br>
Finally, this web map can also be saved as a html webpage.

In [0]:
crime_map.save('phx_crime_map_folium.html')